In [1]:
#aysenur

In [1]:
import time 

import pytorch_lightning as pl

from pytorch_lightning.callbacks.early_stopping import EarlyStopping
from pytorch_lightning.callbacks import ModelCheckpoint

from pytorch_lightning.loggers import WandbLogger
import wandb

/home/aysenurk/anaconda3/lib/python3.8/site-packages/setuptools/distutils_patch.py:25: UserWarning: Distutils was imported before Setuptools. This usage is discouraged and may exhibit undesirable behaviors or errors. Please use Setuptools' objects directly or at least import Setuptools first.
  warnings.warn(


In [2]:
from src.TimeSeriesLearningUtils import *
from src.LSTMModel import *

In [3]:
def name_model(config):
    name =[]
    if len(config["currency_list"])  > 1:
        name.append("multi_task_" + "_".join(config["currency_list"]))
    else:
        name.append(config["currency_list"][0])
        
    if config["indicators"] or config["imfs"] or config ["ohlv"]:
        name.append("multi_variate")
    
    lstm = "stack_lstm" if config["n_lstm_layers"] > 1 else "lstm"
    name.append(lstm)
    
    name.append(config["pred_frequency"])
    classification = "multi_clf" if config["num_classes"] > 2 else "binary_clf"
    name.append(classification)
    
    return "_".join(name)

In [22]:
WANDBPROJECT = "v1"

In [28]:
def experiment(config):    
    X, y, features, dfs = get_data(**config)
    train_dataset, val_dataset, test_dataset = [TimeSeriesDataset(X,
                                                                  y,
                                                                  dtype, 
                                                                  **config) for dtype in ['train', 'val', 'test']]

    config["dataset_sizes"] = [len(train_dataset), len(val_dataset), len(test_dataset)]
    MODEL_NAME = name_model(config)
    
    wandb.init(project=WANDBPROJECT,######
               config=config,
               entity='multi_task_price_prediction',
               name = MODEL_NAME )

    logger = WandbLogger()

    model = LSTM_based_classification_model(train_dataset = train_dataset,
                                            val_dataset = val_dataset,
                                            test_dataset = test_dataset,
                                            **config)

    early_stop_callback = EarlyStopping(
       monitor='val_loss',
       min_delta=0.003,
       patience=10,
       verbose=True,
       mode='min'
    )
    checkpoint_callback = ModelCheckpoint(
        monitor='val_loss',
        dirpath='../output/',
        filename = MODEL_NAME + str(time.time()) +'-{epoch:02d}-{val_loss:.2f}',
        save_top_k=1,
        mode='min',
    )

    trainer = pl.Trainer(gpus=-1, 
                         max_epochs= 80,
                         logger = logger, 
                         callbacks=[early_stop_callback, checkpoint_callback])
    trainer.fit(model)

    trainer.test(ckpt_path = checkpoint_callback.best_model_path)

    wandb.finish()

In [29]:
CONFIG = {#fix for this project
          "window_size": 50, 
          "dataset_percentages": [0.96, 0.02, 0.02],
          "data_frequency": "6h", 
          "pred_frequency": "6h", 
          "ma_period": 7,
          "neutral_quantile": 0.33,
          "batch_size": 64,
          "log_price": True,
          "dropout_after_each_lstm_layer": 0.1,
          "dropout_before_output_layer": 0.1,
          "last_layer_fsz": 32,
          "warmup_epoch": 10,
          "learning_rate": 1e-3,
          "weight_decay": 1e-2,
          "imfs": False, 
          "ohlv": True, # trend bunlardan da çıkarılıyor mu?
          "remove_trend": True}

In [30]:
from sklearn.model_selection import ParameterGrid
param_grid = {"num_classes": [2,3],
          "currency_list": [['BTC'], ['ETH'], ['LTC'],  ['BTC', 'ETH', 'LTC']],
          
          "lstm_hidden_size": [64, 128],
          "n_lstm_layers": [1,3,5],
          "calculate_loss_weights": [True, False],
          "indicators": [True, False],
          "bidirectional":[True, False]}

In [20]:
ParameterGrid(param_grid).__len__()

384

In [ ]:
for c in (ParameterGrid(param_grid)):
    config = CONFIG.copy()
    config.update(c)

    experiment(config)

/home/aysenurk/anaconda3/lib/python3.8/site-packages/ta/trend.py:768: RuntimeWarning: invalid value encountered in double_scalars
  dip[i] = 100 * (self._dip[i] / self._trs[i])
/home/aysenurk/anaconda3/lib/python3.8/site-packages/ta/trend.py:772: RuntimeWarning: invalid value encountered in double_scalars
  din[i] = 100 * (self._din[i] / self._trs[i])


wandb: wandb version 0.12.0 is available!  To upgrade, please run:
wandb:  $ pip install wandb --upgrade


/home/aysenurk/anaconda3/lib/python3.8/site-packages/pytorch_lightning/callbacks/model_checkpoint.py:446: UserWarning: Checkpoint directory ../output/ exists and is not empty.
  rank_zero_warn(f"Checkpoint directory {dirpath} exists and is not empty.")
GPU available: True, used: True
TPU available: False, using: 0 TPU cores
IPU available: False, using: 0 IPUs
LOCAL_RANK: 0 - CUDA_VISIBLE_DEVICES: [0]

  | Name               | Type       | Params
--------------------------------------------------
0 | lstm_blocks        | ModuleList | 79.1 K
1 | linear1            | ModuleList | 4.1 K 
2 | activation         | ReLU       | 0     
3 | dropout1           | Dropout    | 0     
4 | output_layers      | ModuleList | 66    
5 | cross_entropy_loss | ModuleList | 0     
6 | f1_score           | F1         | 0     
7 | accuracy_score     | Accuracy   | 0     
--------------------------------------------------
83.3 K    Trainable params
0         Non-trainable params
83.3 K    Total params
0.333  

/home/aysenurk/anaconda3/lib/python3.8/site-packages/pytorch_lightning/trainer/data_loading.py:105: UserWarning: The dataloader, val dataloader 0, does not have many workers which may be a bottleneck. Consider increasing the value of the `num_workers` argument` (try 12 which is the number of cpus on this machine) in the `DataLoader` init to improve performance.
  rank_zero_warn(
/home/aysenurk/anaconda3/lib/python3.8/site-packages/pytorch_lightning/trainer/data_loading.py:105: UserWarning: The dataloader, train dataloader, does not have many workers which may be a bottleneck. Consider increasing the value of the `num_workers` argument` (try 12 which is the number of cpus on this machine) in the `DataLoader` init to improve performance.
  rank_zero_warn(


Metric val_loss improved. New best score: 0.697


...

/home/aysenurk/anaconda3/lib/python3.8/site-packages/ta/trend.py:768: RuntimeWarning: invalid value encountered in double_scalars
  dip[i] = 100 * (self._dip[i] / self._trs[i])
/home/aysenurk/anaconda3/lib/python3.8/site-packages/ta/trend.py:772: RuntimeWarning: invalid value encountered in double_scalars
  din[i] = 100 * (self._din[i] / self._trs[i])
wandb: wandb version 0.12.0 is available!  To upgrade, please run:
wandb:  $ pip install wandb --upgrade


/home/aysenurk/anaconda3/lib/python3.8/site-packages/pytorch_lightning/callbacks/model_checkpoint.py:446: UserWarning: Checkpoint directory ../output/ exists and is not empty.
  rank_zero_warn(f"Checkpoint directory {dirpath} exists and is not empty.")
GPU available: True, used: True
TPU available: False, using: 0 TPU cores
IPU available: False, using: 0 IPUs
LOCAL_RANK: 0 - CUDA_VISIBLE_DEVICES: [0]

  | Name               | Type       | Params
--------------------------------------------------
0 | lstm_blocks        | ModuleList | 376 K 
1 | linear1            | ModuleList | 4.1 K 
2 | activation         | ReLU       | 0     
3 | dropout1           | Dropout    | 0     
4 | output_layers      | ModuleList | 99    
5 | cross_entropy_loss | ModuleList | 0     
6 | f1_score           | F1         | 0     
7 | accuracy_score     | Accuracy   | 0     
--------------------------------------------------
380 K     Trainable params
0         Non-trainable params
380 K     Total params
1.523  

/home/aysenurk/anaconda3/lib/python3.8/site-packages/pytorch_lightning/trainer/data_loading.py:105: UserWarning: The dataloader, val dataloader 0, does not have many workers which may be a bottleneck. Consider increasing the value of the `num_workers` argument` (try 12 which is the number of cpus on this machine) in the `DataLoader` init to improve performance.
  rank_zero_warn(
/home/aysenurk/anaconda3/lib/python3.8/site-packages/pytorch_lightning/trainer/data_loading.py:105: UserWarning: The dataloader, train dataloader, does not have many workers which may be a bottleneck. Consider increasing the value of the `num_workers` argument` (try 12 which is the number of cpus on this machine) in the `DataLoader` init to improve performance.
  rank_zero_warn(


Metric val_loss improved. New best score: 1.088


Metric val_loss improved by 0.012 >= min_delta = 0.003. New best score: 1.076
